In [ ]:
!pip install datasets
!pip install kagglehub
!pip install transformers torch torchvision accelerate
!pip uninstall diffusers -y
!pip install git+https://github.com/huggingface/diffusers.git@main # need latest version

In [2]:
import os
import pandas as pd
from diffusers import StableDiffusionPipeline
import torch

import kagglehub
import shutil

In [3]:
device = torch.device("cpu")
if torch.backends.mps.is_available():
    device = torch.device("mps")
elif torch.cuda.is_available():
    device = torch.device("cuda")
assert str(device)=='cuda' or str(device)=='mps', f"{device}" # need a GPU!
print(device)

cuda


In [4]:
# DATASET AT https://www.kaggle.com/datasets/sartajbhuvaji/brain-tumor-classification-mri
# OR RUN FOLLOWING TO DOWNLOAD IT:

# Download latest version
path = kagglehub.dataset_download("sartajbhuvaji/brain-tumor-classification-mri")

# Get the current working directory
current_dir = os.getcwd()
new_path = os.path.join(current_dir, "archive")

# Move the downloaded directory to the current directory
shutil.move(path, new_path)

print("Path to dataset files:", new_path)

100%|██████████| 86.8M/86.8M [00:04<00:00, 18.4MB/s]

Extracting files...


Path to dataset files: /content/archive


In [5]:
#!ls archive/Training/* | wc -l
import subprocess

# Run the command and capture its output
result = subprocess.run("ls archive/Training/* | wc -l", shell=True, capture_output=True, text=True)

# Convert the output to an integer
file_count = int(result.stdout.strip())

# Assert that the file count is 2877
assert file_count == 2877, f"Expected 2877 files, but found {file_count}"

In [7]:
N_CLASSES = 4
assert N_CLASSES==4

In [9]:
# Run training optimized for A100 with batch 32
# FOR HIGH QUALITY IMAGES:
#  20 epochs (num train epochs is overwritten)
# 2870 ÷ 32 ≈ 89.6875 (rounds to 90 steps per epoch), 90steps/epoch
# Total steps ÷ Steps per epoch = 1800 ÷ 90 ≈ 20 epochs.
!python TESTING_train_text_to_image.py \
   --pretrained_model_name_or_path="runwayml/stable-diffusion-v1-5" \
   --train_data_dir="." \
   --dataset_name="csv" \
   --dataset_config_name="fine_tuning_metadata_A100_2870.csv" \
   --image_column="image_path" \
   --caption_column="prompt" \
   --resolution=256 \
   --train_batch_size=32 \
   --num_train_epochs=1 \
   --learning_rate=1e-5 \
   --max_train_steps=1800 \
   --output_dir="fine_tuned_model_A100_2870" \
   --checkpointing_steps=900 \
   --mixed_precision="fp16"


2025-03-09 17:45:01.695471: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1741542301.717629    4638 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1741542301.724285    4638 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
03/09/2025 17:45:07 - INFO - __main__ - Distributed environment: DistributedType.NO
Num processes: 1
Process index: 0
Local process index: 0
Device: cuda

Mixed precision type: fp16

scheduler_config.json: 100% 308/308 [00:00<00:00, 2.33MB/s]
{'dynamic_thresholding_ratio', 'thresholding', 'variance_type', 'timestep_spacing', 'rescale_betas_zero_snr', 'prediction_type', 'sample_max_value', 'clip_sample_range'} was not found in config.

In [10]:
#Total amount of image prompt pairs: 800, 200 per class (4 classes total)
!python TESTING_train_text_to_image.py \
    --pretrained_model_name_or_path="runwayml/stable-diffusion-v1-5" \
    --train_data_dir="." \
    --dataset_name="csv" \
    --dataset_config_name="fine_tuning_metadata_A100_800.csv" \
    --image_column="image_path" \
    --caption_column="prompt" \
    --resolution=256 \
    --train_batch_size=16 \
    --num_train_epochs=1 \
    --learning_rate=1e-6 \
    --max_train_steps=4000 \
    --output_dir="fine_tuned_model_A100_800" \
    --checkpointing_steps=2000 \
    --mixed_precision="fp16" \
    --gradient_checkpointing


2025-03-09 18:03:18.908659: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1741543398.930018    9302 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1741543398.936556    9302 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
03/09/2025 18:03:22 - INFO - __main__ - Distributed environment: DistributedType.NO
Num processes: 1
Process index: 0
Local process index: 0
Device: cuda

Mixed precision type: fp16

{'prediction_type', 'sample_max_value', 'dynamic_thresholding_ratio', 'clip_sample_range', 'variance_type', 'timestep_spacing', 'rescale_betas_zero_snr', 'thresholding'} was not found in config. Values will be initialized to default values.
Instantiating

In [11]:
!python TESTING_train_text_to_image.py \
    --pretrained_model_name_or_path="runwayml/stable-diffusion-v1-5" \
    --train_data_dir="." \
    --dataset_name="csv" \
    --dataset_config_name="fine_tuning_metadata_MPS_248.csv" \
    --image_column="image_path" \
    --caption_column="prompt" \
    --resolution=256 \
    --train_batch_size=32 \
    --num_train_epochs=1 \
    --learning_rate=1e-6 \
    --max_train_steps=500 \
    --output_dir="fine_tuned_model_MPS_248" \
    --checkpointing_steps=250 \
    --mixed_precision="fp16"



2025-03-09 18:33:37.142035: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1741545217.164142   17037 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1741545217.170690   17037 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
03/09/2025 18:33:41 - INFO - __main__ - Distributed environment: DistributedType.NO
Num processes: 1
Process index: 0
Local process index: 0
Device: cuda

Mixed precision type: fp16

{'thresholding', 'dynamic_thresholding_ratio', 'variance_type', 'timestep_spacing', 'rescale_betas_zero_snr', 'prediction_type', 'sample_max_value', 'clip_sample_range'} was not found in config. Values will be initialized to default values.
Instantiating

In [18]:
######## TODO RM -RF THE CHECKPOINTS!
#!rm -rf fine_tuned_model_MPS_248/checkpoint-500
#!rm -rf fine_tuned_model_A100_800/checkpoint-4000
    #('fine_tuned_model_A100_800

# Generate new images using fine-tuned model

In [19]:
from diffusers import StableDiffusionPipeline
import torch
#from google.colab import drive
import os
from tqdm import tqdm

In [20]:
device = "cuda" if torch.cuda.is_available() else "cpu"
if torch.backends.mps.is_available():
    device = torch.device("mps")
print(f"Using device: {device}")
assert str(device)=="cuda" or str(device)=="mps"

Using device: cuda


## TO GET MODEL FROM GOOGLE DRIVE (not recommended since models take up too much space)

In [ ]:
models = [
    ('fine_tuned_model_A100_800', torch.float16),  # A100 TRAINED ON FP16
    ('fine_tuned_model_MPS_248', torch.float32) # MPS trained on FP32
]

model_type, dtype= models[0]

In [ ]:
# GET FINE-TUNED MODEL FROM GOOGLE DRIVE

drive.mount('/content/drive')


model_path = os.path.join('/content/drive/MyDrive/', model_type)

# Check if the folder exists
if os.path.exists(model_path):
  print(f"The folder '{model_path}' exists.")
else:
  print(f"The folder '{model_path}' does not exist. Please check the path.")


Mounted at /content/drive
The folder '/content/drive/MyDrive/fine_tuned_model_A100_800' exists.


'if os.path.exists(checkpoint_path):\n    print(f"The folder \'{checkpoint_path}\' exists.")\nelse:\n    print(f"The folder \'{checkpoint_path}\' does not exist. Please check the path.")\n    '

In [ ]:
print(model_path)
GPU_numImagesTrainedOn = model_type[17:] # GPU_numImagesTrainedOn
print(GPU_numImagesTrainedOn)

/content/drive/MyDrive/fine_tuned_model_A100_800
A100_800


In [ ]:
!ls {model_path}

checkpoint-2000  feature_extractor  model_index.json  scheduler     tokenizer  vae
checkpoint-4000  logs		    safety_checker    text_encoder  unet


In [ ]:
!ls {model_path}/unet

config.json  diffusion_pytorch_model.safetensors


## TO GET FINE TUNED MODEL FROM CURRENT DIR

In [21]:
models = [
    ('fine_tuned_model_MPS_248','MPS', 248, torch.float16),
    ('fine_tuned_model_A100_2870','A100', 2870, torch.float16),
    ('fine_tuned_model_A100_800','A100', 800, torch.float16)
]



#model_path, GPU_numImagesTrainedOn, dtype = models[0]

In [22]:

prompts = {
    "glioma_tumor": "MRI of brain with glioma tumor",
    "meningioma_tumor": "MRI of brain with meningioma tumor",
    "pituitary_tumor": "MRI of brain with pituitary tumor",
    "no_tumor": "MRI of brain with no tumor"
}
N_CLASSES=4
assert N_CLASSES==4

## Generate new images!

In [26]:
"""
THIS CELL NEEDS TO BE RUN ON A100 WITH ALL 3 MODELS IN THE CURRENT DIR
CAN USE OTHER IPYNB TO GET THE MODELS

THIS CELL WILL DO THE FOLLOWING:
FOR EACH MODEL, CREATE DIR AND SUBDIRS TO STORE SYNTHETIC IMAGES,
THEN GENERATE THE IMAGES AND STORE THEM IN APPROPRIATE DIR
FOR ONE MODEL, DIR STRUCTURE:
post_fine_tuning_images_A100_2870
├── glioma_tumor
├── meningioma_tumor
├── no_tumor
└── pituitary_tumor
"""


ratioSyntheticToReal=3 # 3x more synthetic data than real data
print(f"Generating {ratioSyntheticToReal} synthetic images for every real image...\n")
print(device)
for model_path, GPU, numImagesTrainedOn, dtype in models:
    print(f"Loading model {model_path}...")
    # Load fine-tuned model

    sd_model_ft = StableDiffusionPipeline.from_pretrained(model_path, torch_dtype=dtype)
    sd_model_ft = sd_model_ft.to(device)

    # make dirs
    dir_name = f"post_fine_tuning_images_{GPU}_{numImagesTrainedOn}"
    os.makedirs(dir_name, exist_ok=True)
    for label in prompts.keys():
        os.makedirs(os.path.join(dir_name, label), exist_ok=True)# make subdirectories

    numSyntheticImages = ratioSyntheticToReal * numImagesTrainedOn
    numSyntheticImagesPerClass = int(numSyntheticImages/N_CLASSES)# for each class (equal num of synthetic image per class)
    print(f"Generating {numSyntheticImages} synthetic images using: {model_path}, {numSyntheticImagesPerClass} per class")

    batch_size = 32  # Safe for A100’s 40 GB
    for label, prompt in prompts.items():
        image_path = os.path.join(dir_name, label)
        print(f"\tGenerating images at {image_path}")
        print(f"\tusing prompt '{prompt}'")

        # batch generation of images
        total_batches = (numSyntheticImagesPerClass + batch_size - 1) // batch_size  # Ceiling division
        for start_idx in tqdm(range(0, numSyntheticImagesPerClass, batch_size), total=total_batches, desc=f"Generating {label}"):

            batch_count = min(batch_size, numSyntheticImagesPerClass - start_idx)
            #print(f"\t\t{batch_count}")
            images = sd_model_ft(prompt, num_inference_steps=50, guidance_scale=7.5,
                                num_images_per_prompt=batch_count, disable=True).images
            for i, image in enumerate(images):
                image.save(os.path.join(image_path, f"image_{label}_{start_idx + i}.jpg"))
    print("-"*80)

Generating 3 synthetic images for every real image...

cuda
Loading model fine_tuned_model_MPS_248...


Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

Generating 744 synthetic images using: fine_tuned_model_MPS_248, 186 per class
	Generating images at post_fine_tuning_images_MPS_248/glioma_tumor
	using prompt 'MRI of brain with glioma tumor'


Generating glioma_tumor:   0%|          | 0/6 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

...

  0%|          | 0/50 [00:00<?, ?it/s]

Generating no_tumor:  95%|█████████▍| 18/19 [07:18<00:24, 24.36s/it]

  0%|          | 0/50 [00:00<?, ?it/s]

Generating no_tumor: 100%|██████████| 19/19 [07:36<00:00, 24.05s/it]

--------------------------------------------------------------------------------


In [33]:
####### confirm there are correct number
!find post_fine_tuning_images_MPS_248 -type f | wc -l && echo "Expected: 744"
!find post_fine_tuning_images_A100_800 -type f | wc -l && echo "Expected: 2400"
!find post_fine_tuning_images_A100_2870 -type f | wc -l && echo "Expected: 8610"

744
Expected: 744
2400
Expected: 2400
8610
Expected: 8610


In [34]:
#####MOUNT GOOGLE DRIVE TO SAVE THE POST FINE TUNING IMAGES
import os
import shutil
from google.colab import drive

# Mount Google Drive
print("Mounting Google Drive...")
drive.mount('/content/drive')

# Define the folders to save
folders_to_save = [
    'post_fine_tuning_images_MPS_248',
    'post_fine_tuning_images_A100_800',
    'post_fine_tuning_images_A100_2870'
]

# Save folders to Google Drive
drive_base_path = '/content/drive/MyDrive/synthetic_mri_images/'  # Adjust path as needed
os.makedirs(drive_base_path, exist_ok=True)

for dir_name in folders_to_save:
    zip_name = f"{dir_name}.zip"
    print(f"Zipping {dir_name} to {zip_name}...")
    shutil.make_archive(dir_name, 'zip', dir_name)  # Zip the folder
    drive_zip_path = os.path.join(drive_base_path, zip_name)
    print(f"Saving {zip_name} to {drive_zip_path}...")
    shutil.move(zip_name, drive_zip_path)  # Move zip to Drive
    print(f"Saved {dir_name} to Google Drive!")

print("All folders saved to Google Drive!")

Mounting Google Drive...
Mounted at /content/drive
Zipping post_fine_tuning_images_MPS_248 to post_fine_tuning_images_MPS_248.zip...
Saving post_fine_tuning_images_MPS_248.zip to /content/drive/MyDrive/synthetic_mri_images/post_fine_tuning_images_MPS_248.zip...
Saved post_fine_tuning_images_MPS_248 to Google Drive!
Zipping post_fine_tuning_images_A100_800 to post_fine_tuning_images_A100_800.zip...
Saving post_fine_tuning_images_A100_800.zip to /content/drive/MyDrive/synthetic_mri_images/post_fine_tuning_images_A100_800.zip...
Saved post_fine_tuning_images_A100_800 to Google Drive!
Zipping post_fine_tuning_images_A100_2870 to post_fine_tuning_images_A100_2870.zip...
Saving post_fine_tuning_images_A100_2870.zip to /content/drive/MyDrive/synthetic_mri_images/post_fine_tuning_images_A100_2870.zip...
Saved post_fine_tuning_images_A100_2870 to Google Drive!
All folders saved to Google Drive!
